In [8]:
import sys
import os
import tiktoken
sys.path.insert(0, os.path.abspath('..'))

from strategies import InstructionFollowingStrategy
from trainer import SingleHeadTrainer
from data_utils import create_dataloaders


def get_vocab_size(encoding_name="gpt2"):
    tokenizer = tiktoken.get_encoding(encoding_name)
    return tokenizer.n_vocab


In [9]:
vocab_size = get_vocab_size("gpt2")
tokenizer = tiktoken.get_encoding("gpt2")
pad_token_id=50256

strategy = InstructionFollowingStrategy(
    tokenizer=tokenizer,
    instruction_token="[INST]",
    response_token="[/INST]",
    end_token="</s>",
    pad_token_id=pad_token_id,
    max_length=2048,
)



train_loader, val_loader, train_sampler, val_sampler = create_dataloaders(
    files_pattern="/home/alexander/Tank3/training_data/instruction_completion/*.jsonl",
    block_size=2048,
    batch_size=4,
    rank=1,
    world_size=1,
    strategy=strategy,
    tokenizer=tokenizer,
    n_aux_heads=16,
    prefetch_factor=1,
    num_workers=1,
    use_news=False
)

Encoding instruction token '[INST]': [58, 38604, 60]
Encoding response token '[/INST]': [13412, 38604, 60]
Final instruction token ID: 58
Final response token ID: 13412
Loading instruction data...

Loading local instruction files matching pattern: /home/alexander/Tank3/training_data/instruction_completion/*.jsonl
Found 21 files to process
Processed 1000 examples, created 1000 chunks
Processed 2000 examples, created 2000 chunks
Processed 3000 examples, created 3000 chunks
Processed 4000 examples, created 4000 chunks
Processed 5000 examples, created 5000 chunks
Processed 6000 examples, created 6000 chunks
Processed 7000 examples, created 7000 chunks
Processed 8000 examples, created 8000 chunks
Processed 9000 examples, created 9000 chunks
Processed 10000 examples, created 10000 chunks
Processed 11000 examples, created 11000 chunks
Processed 12000 examples, created 12000 chunks
Processed 13000 examples, created 13000 chunks
Processed 14000 examples, created 14000 chunks
Processed 15000 exa

In [10]:
first_batch = next(iter(train_loader))
first_batch


{'inputs': tensor([[   58, 38604,    60,  ..., 50256, 50256, 50256],
         [   58, 38604,    60,  ..., 50256, 50256, 50256],
         [   58, 38604,    60,  ..., 50256, 50256, 50256],
         [   58, 38604,    60,  ..., 50256, 50256, 50256]]),
 'targets': tensor([[38604,    60, 21017,  ..., 50256, 50256, 50256],
         [38604,    60, 21017,  ..., 50256, 50256, 50256],
         [38604,    60, 21017,  ..., 50256, 50256, 50256],
         [38604,    60, 21017,  ..., 50256, 50256, 50256]]),
 'future_targets': [tensor([[   60, 21017, 46486,  ..., 50256, 50256, 50256],
          [   60, 21017, 46486,  ..., 50256, 50256, 50256],
          [   60, 21017, 46486,  ..., 50256, 50256, 50256],
          [   60, 21017, 46486,  ..., 50256, 50256, 50256]]),
  tensor([[21017, 46486,    25,  ..., 50256, 50256, 50256],
          [21017, 46486,    25,  ..., 50256, 50256, 50256],
          [21017, 46486,    25,  ..., 50256, 50256, 50256],
          [21017, 46486,    25,  ..., 50256, 50256, 50256]]),
 

In [12]:
input_tokens = first_batch["inputs"][0].cpu().tolist()
target_tokens = first_batch["targets"][0].cpu().tolist()
attention_mask = first_batch["attention_mask"][0].cpu().tolist()

In [20]:
while input_tokens and input_tokens[-1] == pad_token_id:
    input_tokens.pop()

while target_tokens and target_tokens[-1] == pad_token_id:
    target_tokens.pop()

In [33]:
print(input_tokens[410:460])
print(target_tokens[410:460])

[1276, 7773, 6687, 4133, 290, 10039, 22867, 284, 3368, 43656, 742, 3004, 290, 4155, 326, 649, 33787, 10548, 351, 6467, 3815, 290, 2055, 4661, 3693, 14, 38604, 60, 3556, 82, 29]
[7773, 6687, 4133, 290, 10039, 22867, 284, 3368, 43656, 742, 3004, 290, 4155, 326, 649, 33787, 10548, 351, 6467, 3815, 290, 2055, 4661, 3693, 14, 38604, 60, 3556, 82, 29]


In [23]:
print(tokenizer.decode(input_tokens))
print("-"*80)
print(tokenizer.decode(target_tokens))

[INST]### Instruction:
Consider a scenario where a sovereign tribal nation, traditionally reliant on casino revenues, faces a sudden and complete shutdown of its gambling operations due to an unforeseen global event. In response, the tribal leadership decides to pursue rapid diversification into various non-gambling sectors, such as federal government contracting, retail, manufacturing, and health care. Assume that significant resources and strategic partnerships are allocated to establish a robust presence in these areas within a year. Given this context, analyze the potential outcomes and systemic impacts on the tribal economy, employment, and long-term sustainability. Consider the roles of key stakeholders, including tribal leaders, businesses, and federal agencies. What are the possible benefits and challenges the tribe might encounter? How might these changes influence the broader community and relationships with external entities?

### Response:
In this counterfactual scenario, t

In [17]:
last_input_token = input_tokens[-1]
target_token = target_tokens[
    -1
]  # First target token corresponds to last input token

print("\nToken-by-token alignment:")
print(f"Last input token: '{tokenizer.decode([last_input_token])}'")
print(f"Expected next token: '{tokenizer.decode([target_token])}'")


Token-by-token alignment:
Last input token: '>'
Expected next token: '<|endoftext|>'


In [ ]:
self._log_next_token_debug(
                            model,
                            tokenizer,
                            input_tokens,
                            target_tokens,
                            self.strategy,
                            future_targets=(
                                [ft[0] for ft in future_targets]
                                if future_targets
                                else None
                            ),
                            sample_idx=0,
                            num_aux_heads=num_aux_heads,
                            block_size=block_size,
                        )

In [46]:
import torch
from typing import List, Optional, Tuple
import numpy as np
import matplotlib.pyplot as plt
from IPython.display import display, HTML

class InstructionAttentionInspector:
    def __init__(self, tokenizer):
        self.tokenizer = tokenizer
        plt.rcParams['figure.figsize'] = [12, 8]
        
    def find_instruction_length(self, input_tokens: List[int]) -> int:
        """
        Finds the instruction length by locating the '### Response:' marker.
        Returns the position after the marker.
        """
        # Get the full text
        full_text = self.tokenizer.decode(input_tokens)
        
        # Find the marker position
        marker = "### Response:"
        marker_pos = full_text.find(marker)
        
        if marker_pos == -1:
            raise ValueError("Could not find '### Response:' marker in the sequence")
            
        # Get the text up to and including the marker
        instruction_text = full_text[:marker_pos + len(marker)]
        
        # Count tokens up to this position by encoding and checking length
        instruction_tokens = self.tokenizer.encode(instruction_text)
        instruction_length = len(instruction_tokens)
        
        return instruction_length

    def create_attention_pattern(self, 
                               input_tokens: List[int],
                               instruction_length: int,
                               padding_mask: List[int]) -> np.ndarray:
        """
        Creates the expected attention pattern matrix.
        """
        seq_len = len(input_tokens)
        attention_matrix = np.zeros((seq_len, seq_len))
        
        for i in range(seq_len):
            if padding_mask[i] == 0:  # Skip padding tokens
                continue
                
            if i < instruction_length:
                # Instruction tokens can attend to all instruction tokens
                attention_matrix[i, :instruction_length] = 1
            else:
                # Completion tokens can attend to all instruction tokens
                attention_matrix[i, :instruction_length] = 1
                # And causally to previous completion tokens
                attention_matrix[i, instruction_length:i+1] = 1
                
        # Apply padding mask
        attention_matrix *= np.array(padding_mask).reshape(1, -1)
        return attention_matrix

    def visualize_attention(self,
                          input_tokens: List[int],
                          instruction_length: int,
                          padding_mask: List[int],
                          max_display: Optional[int] = None,
                          title: str = 'Instruction-Completion Attention Pattern'):
        """
        Visualizes the attention pattern with token labels.
        """
        plt.clf()
        
        # Decode tokens for labels
        tokens = [self.tokenizer.decode([t]) for t in input_tokens]
        tokens = [t.replace('▁', ' ').strip() for t in tokens]
        
        # Create attention pattern
        attention_matrix = self.create_attention_pattern(input_tokens, instruction_length, padding_mask)
        
        # Limit display size if needed
        if max_display:
            attention_matrix = attention_matrix[:max_display, :max_display]
            tokens = tokens[:max_display]
        
        plt.figure(figsize=(12, 8))
        plt.imshow(attention_matrix, cmap='Blues', aspect='auto')
        plt.colorbar(label='Attention Allowed (1=Yes, 0=No)')
        
        # Set ticks and labels
        plt.xticks(range(len(tokens)), tokens, rotation=45, ha='right')
        plt.yticks(range(len(tokens)), tokens)
        
        # Add lines to separate instruction from completion
        plt.axvline(x=instruction_length - 0.5, color='red', linestyle='--', alpha=0.5)
        plt.axhline(y=instruction_length - 0.5, color='red', linestyle='--', alpha=0.5)
        
        plt.title(title)
        plt.xlabel('Target Token (Key)')
        plt.ylabel('Source Token (Query)')
        
        plt.tight_layout()
        display(plt.gcf())
        plt.close()
        
    def display_sequence_info(self,
                            input_tokens: List[int],
                            instruction_length: int,
                            padding_mask: List[int]):
        """
        Displays sequence information in a Jupyter-friendly format.
        """
        tokens = [self.tokenizer.decode([t]) for t in input_tokens]
        
        # Create HTML table for token information
        html = """
        <style>
            .token-table { width: 100%; border-collapse: collapse; margin: 10px 0; }
            .token-table th, .token-table td { border: 1px solid #ddd; padding: 8px; text-align: left; }
            .token-table th { background-color: #f5f5f5; }
            .instruction { background-color: #e6f3ff; }
            .completion { background-color: #fff; }
            .marker { background-color: #ffe6e6; }
        </style>
        """
        
        # Add summary information
        html += f"""
        <h3>Sequence Analysis</h3>
        <p>
        Total sequence length: {len(input_tokens)}<br>
        Instruction length (including response marker): {instruction_length}<br>
        Completion length: {len(input_tokens) - instruction_length}
        </p>
        """
        
        # Create token table
        html += """
        <table class='token-table'>
            <tr>
                <th>Position</th>
                <th>Token</th>
                <th>Token ID</th>
                <th>Mask</th>
                <th>Section</th>
            </tr>
        """
        
        full_text = self.tokenizer.decode(input_tokens)
        marker_text = "### Response:"
        marker_start = full_text.find(marker_text)
        marker_end = marker_start + len(marker_text) if marker_start != -1 else -1
        
        for i, token in enumerate(tokens):
            # Determine if this token is part of the response marker
            token_start = len(self.tokenizer.decode(input_tokens[:i]))
            token_end = len(self.tokenizer.decode(input_tokens[:i+1]))
            is_marker = (token_start >= marker_start and token_start < marker_end) or \
                       (token_end > marker_start and token_end <= marker_end)
            
            if is_marker:
                section_class = "marker"
                section_name = "Response Marker"
            else:
                section_class = "instruction" if i < instruction_length else "completion"
                section_name = "Instruction" if i < instruction_length else "Completion"
                
            html += f"""
            <tr class='{section_class}'>
                <td>{i}</td>
                <td>{token}</td>
                <td>{input_tokens[i]}</td>
                <td>{padding_mask[i]}</td>
                <td>{section_name}</td>
            </tr>
            """
        
        html += "</table>"
        display(HTML(html))
        
    def analyze_sequence(self,
                        input_tokens: List[int],
                        padding_mask: List[int],
                        max_display: Optional[int] = None):
        """
        Complete analysis with automatic instruction length detection.
        """
        # Automatically detect instruction length
        instruction_length = self.find_instruction_length(input_tokens)
        
        # Display sequence information
        self.display_sequence_info(input_tokens, instruction_length, padding_mask)
        
        # Show attention visualization
        self.visualize_attention(
            input_tokens=input_tokens,
            instruction_length=instruction_length,
            padding_mask=padding_mask,
            max_display=max_display
        )
        
        return instruction_length  # Return the detected length for reference

In [47]:
# Import and setup
%matplotlib inline

# Create inspector
inspector = InstructionAttentionInspector(tokenizer)

# Analyze your sequence
instruction_length = inspector.analyze_sequence(
    input_tokens=input_tokens,
    padding_mask=attention_mask,
    max_display=30  # optional
)

ValueError: operands could not be broadcast together with shapes (441,441) (1,4194304) (441,441) 